# Setup

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import os
import re
import json
!pip install pdfplumber
import pdfplumber
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import concurrent.futures
from functools import partial

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.0/42.0 kB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.5/48.5 kB 3.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.2/59.2 kB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 57.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.8/2.8 MB 60.7 MB/s eta 0:00:00


In [ ]:
!pip install nltk
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.tokenize import sent_tokenize

nltk.download('stopwords')
nltk.download('punkt')
nltk.download('punkt_tab')

# Get Portuguese stop words
portuguese_stop_words = set(stopwords.words('portuguese'))
english_stop_words = set(stopwords.words('english'))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


# Call Functions

In [ ]:
def clean(text):

    text = text.replace("\n", ' ')
    text = text.replace("”", '')
    text = text.replace("“", '')
    text = text.replace("\"", '')
    text = text.replace("", '')

    #lista com bolinha
    text = re.sub(r'(\s)?(;\s)?(•)', "; ", text.strip())
    text = re.sub(r'(: ;)', ": ", text.strip())
    text = re.sub(r'(\.;)', ". ", text.strip())

    # nu-2021-4T21-Script 4T21.pdf
    text = re.sub(r'(; -)', ". ", text.strip())
    text = re.sub(r'(\. -)', ". ", text.strip())
    text = re.sub(r'^(-)', "", text.strip())
    text = re.sub(r'(: \d.)', ': .', text.strip())
    text = re.sub(r'(; e (\d+\.)?)', '.', text.strip())
    text = re.sub(r'(: ●)', '.', text.strip())
    text = re.sub(r'(; ●)', '.', text.strip())
    text = re.sub(r'(●)', '', text.strip())

    text = re.sub("_______________________________________________________________", "", text)

    text = re.sub(r"Sra\.", "Senhora ", text, flags=re.IGNORECASE)
    text = re.sub(r"Sr\.", "Senhor ", text, flags=re.IGNORECASE)
    text = re.sub(r"Srs\.", "Senhores ", text, flags=re.IGNORECASE)
    text = re.sub(r'b\.p\.\s([A-Z])', 'bp. \\1', text).strip()
    text = re.sub('b.p.', 'bp', text).strip()
    text = re.sub('p.p.', 'pp', text).strip()
    text = re.sub('help!', 'help', text).strip() # bmgb -> tirar a exclamação para evitar quebra de sentenças

    text = re.sub('\s+', ' ', text).strip() # deixar por ultimo, pois as substituicoes anteriores podem inserir multiplos espaços

    return text

In [ ]:
def get_sentences(text):
    sentences = sent_tokenize(text, language='portuguese')
    sentences = [s for s in sentences if len(s.strip()) > 2]
    return sentences

def get_tokens(text):
    tokens = word_tokenize(text, language='portuguese')

    return tokens

def get_words(text):
    tokens = get_tokens(text)

    words = [w for w in tokens if w not in string.punctuation]

    return words

def save_text(filename, sentences):
    with open(filename, 'w') as f:
        for row in sentences:
            if row != '':
                f.write(row+'\n')

def generate_stats(text):
    stats = {}
    tokens = get_tokens(text)
    num_tokens = len(tokens)

    stats["tokens"] = num_tokens

    return stats

# LDA

LDA calls for a a bigger need of preprocessing - Lemmatization, tokenization, cleaning

## Preprocessing

### Call functions

In [ ]:
from nltk.tokenize import word_tokenize

### Processing text

In [ ]:
transcript_folder = '/content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/'
transcript_text_folder = "/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_lda/"

if not os.path.exists(transcript_text_folder):
    os.mkdir(transcript_text_folder)

files = os.listdir(transcript_folder)

num_files = len(files)
for i, file in enumerate(files):
    path_transcription = transcript_folder + file

    file_name_parts = file.split("-")
    ticker          = file_name_parts[0].strip()
    trimestre       = file_name_parts[2].strip()

    path_folder_ticker = os.path.join(transcript_text_folder, ticker)

    print(path_folder_ticker, ticker, trimestre)
    print('path_transcription', path_transcription)
    if not os.path.exists(path_folder_ticker):
        os.mkdir(path_folder_ticker)

    print('is_file',os.path.isfile(path_transcription))
    if os.path.isfile(path_transcription):
      print(f"Processando arquivo {i+1} de {num_files}")

      print("*** Extraindo texto do PDF: "+ file)
      path_transcription = transcript_folder + file
      if ticker in ['bbas', 'bbdc']:
          page_data = raw_text_extract(path_transcription)
      else:
          page_data = raw_text_extract(path_transcription, include_tables=True, include_images=False)

      print("*** Limpando o texto")
      text = " ".join(page_data)
      text = clean(text)

      file_path = f"{path_folder_ticker}/{ticker}-{file_name_parts[1]+'-'+trimestre}.txt"

      print("*** Salvando arquivo com a texto")
      with open(file_path, 'w', encoding='utf-8') as file:
          file.write(text)

/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_lda/abcb abcb 3T22
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
is_file True
Processando arquivo 1 de 1
*** Extraindo texto do PDF: abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
*** Limpando o texto
*** Salvando arquivo com a texto
/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_lda/abcb abcb 2T10
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/abcb-2010-2T10-Transcrição da Teleconferência 2T10.pdf
is_file True
Processando arquivo 2 de 1
*** Extraindo texto do PDF: abcb-2010-2T10-Transcrição da Teleconferência 2T10.pdf
*** Limpando o texto
*** Salvando arquivo com a texto
/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_lda/sanb sanb 3T
path_transcription /content/drive/MyDrive

### Call processed text

In [ ]:
transcript_text_folder = "/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_lda/"
files = os.listdir(transcript_text_folder)

texts_as_strings = []

num_files = len(files)
for i, file in enumerate(files):
  for j in os.listdir(f'{transcript_text_folder}{file}'):
    print(j)
    file_path = f'{transcript_text_folder}{file}/{j}'

    if file_path.endswith('.txt'):
      with open(file_path, 'r', encoding='utf-8') as document:
        string_data = document.read()

        tokens = word_tokenize(string_data)
        tokens = [word for word in tokens if word not in portuguese_stop_words]

        joined_tokens = " ".join(tokens)

        texts_as_strings.append(joined_tokens)

abcb-2022-3T22.txt
abcb-2010-2T10.txt
abcb-2013-3T13.txt
abcb-2014-3T14.txt
abcb-2009-1T09.txt
abcb-2008-4T08.txt
abcb-2018-1T18.txt
abcb-2010-4T10.txt
abcb-2016-3T16.txt
abcb-2020-4T20.txt
abcb-2015-4T15.txt
abcb-2022-4T22.txt
abcb-2013-1T13.txt
abcb-2011-3T11.txt
abcb-2011-2T11.txt
abcb-2008-2T08.txt
abcb-2016-4T16.txt
abcb-2016-1T16.txt
abcb-2014-4T14.txt
abcb-2023-1T23.txt
abcb-2014-2T14.txt
abcb-2018-4T18.txt
abcb-2019-4T19.txt
abcb-2010-3T10.txt
abcb-2009-3T09.txt
abcb-2009-4T09.txt
abcb-2019-2T19.txt
abcb-2020-2T20.txt
abcb-2022-2T22.txt
abcb-2012-1T12.txt
abcb-2011-1T11.txt
abcb-2015-3T15.txt
abcb-2017-4T17.txt
abcb-2021-2T21.txt
abcb-2008-1T08.txt
abcb-2017-2T17.txt
abcb-2020-3T20.txt
abcb-2019-1T19.txt
abcb-2021-4T21.txt
abcb-2013-4T13.txt
abcb-2009-2T09.txt
abcb-2021-1T21.txt
abcb-2023-2T23.txt
abcb-2018-2T18.txt
abcb-2015-1T15.txt
abcb-2015-2T15.txt
abcb-2019-3T19.txt
abcb-2012-2T12.txt
abcb-2022-1T22.txt
abcb-2012-4T12.txt
abcb-2010-1T10.txt
abcb-2021-3T21.txt
abcb-2012-3T

### Tf-Idf

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Initialize the TF-IDF vectorizer
vectorizer = TfidfVectorizer()

# Apply TF-IDF to the collection of documents
tfidf_matrix = vectorizer.fit_transform(texts_as_strings)

# Inspect the feature names (unique words)
print(vectorizer.get_feature_names_out())

# Inspect the TF-IDF matrix
print(tfidf_matrix.toarray())

['00' '000' '000ª' ... 'únicos' 'úteis' 'útil']
[[0.         0.00824378 0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 ...
 [0.         0.         0.         ... 0.00910274 0.         0.01457185]
 [0.01161913 0.         0.         ... 0.01401588 0.         0.01121845]
 [0.         0.         0.         ... 0.         0.         0.01404624]]


### Apply LDA

In [ ]:
from sklearn.decomposition import LatentDirichletAllocation

# Step 2: Fit LDA
lda = LatentDirichletAllocation(n_components=5, random_state=42, passes = 20, iterations = 400)
lda.fit(tfidf_matrix)

# Step 3: Inspect topics
terms = vectorizer.get_feature_names_out()
for idx, topic in enumerate(lda.components_):
    print(f"Topic {idx}:")
    print(" ".join([terms[i] for i in topic.argsort()[-10:]]))

TypeError: LatentDirichletAllocation.__init__() got an unexpected keyword argument 'passes'

In [ ]:
from gensim.corpora import Dictionary
from gensim.models import LdaModel

In [ ]:
tokens = []
for i in texts_as_strings[0:100]:
  token = word_tokenize(string_data)
  token = [tok for tok in token if not tok.isdigit()]
  token = [tok for tok in token if len(tok) > 2]
  token = [word for word in token if word not in portuguese_stop_words]
  tokens.append(token)
print(tokens)
dictionary = Dictionary(tokens)

[['apresentação', 'resultados', '1t22', 'operadora', 'boa', 'tarde', 'senhoras', 'senhores', 'bem', 'vindos', 'teleconferência', 'holdings', 'sobre', 'resultados', 'primeiro', 'trimestre', 'webcast', 'hoje', 'acompanhado', 'apresentação', 'slides', 'disponível', 'site', 'investidores', 'www', 'investors', 'inglês', 'www', 'investidores', 'português', 'teleconferência', 'sendo', 'gravada', 'replay', 'disponibilizado', 'site', 'companhia', 'teleconferência', 'disponível', 'português', 'acessar', 'conferência', 'português', 'clique', 'ícone', 'lado', 'inferior', 'direito', 'tela', 'zoom', 'selecione', 'opção', 'portuguese', 'room', 'acessar', 'nova', 'sala', 'esqueça', 'silenciar', 'áudio', 'original', 'informamos', 'todos', 'participantes', 'estarão', 'conectados', 'apenas', 'ouvintes', 'pode', 'enviar', 'perguntas', 'online', 'qualquer', 'momento', 'usando', 'caixa', 'perguntas', 'respostas', 'webcast', 'agora', 'passo', 'palavra', 'senhor', 'guilherme', 'vieira', 'gerente', 'sênior', '

In [ ]:
corpus = [dictionary.doc2bow(text) for text in tokens]

# Train LDA model
lda_model = LdaModel(
    corpus=corpus,
    id2word=dictionary,
    num_topics=20,  # Number of topics
    passes=20,     # Number of passes through the corpus
    iterations=400, # Number of iterations per pass
    random_state=42
)

# Inspect topics
topics = lda_model.show_topics(num_words=5, formatted=False)
for topic_id, words in topics:
    print(f"Topic {topic_id}: {words}")

Topic 17: [('opções', 0.000538793), ('oportunidades', 0.000538793), ('orgânico', 0.000538793), ('opção', 0.000538793), ('orgânicos', 0.000538793)]
Topic 10: [('opções', 0.000538793), ('oportunidades', 0.000538793), ('orgânico', 0.000538793), ('opção', 0.000538793), ('orgânicos', 0.000538793)]
Topic 14: [('opções', 0.000538793), ('oportunidades', 0.000538793), ('orgânico', 0.000538793), ('opção', 0.000538793), ('orgânicos', 0.000538793)]
Topic 16: [('clientes', 0.0013617029), ('crédito', 0.0011520177), ('então', 0.0011426178), ('mercado', 0.00090929214), ('crescimento', 0.00090565364)]
Topic 4: [('clientes', 0.0008334426), ('crédito', 0.0007568041), ('então', 0.00073236204), ('sobre', 0.00073106133), ('mercado', 0.0007056053)]
Topic 15: [('crédito', 0.00053887814), ('clientes', 0.0005388526), ('crescimento', 0.0005388313), ('então', 0.00053883024), ('trimestre', 0.00053882605)]
Topic 12: [('crédito', 0.001041314), ('clientes', 0.00094894273), ('então', 0.0008147244), ('crescimento', 0.0

### Spacy

Lemmatize and preprocess words

In [ ]:
tokens = word_tokenize(cleaned_text)
tokens = [word for word in tokens if word not in portuguese_stop_words]

In [ ]:
!pip install spacy
!python -m spacy download pt_core_news_sm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 31.7 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('pt_core_news_sm')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


In [ ]:
import spacy
# Load Portuguese model
nlp = spacy.load("pt_core_news_sm")

In [ ]:
doc = nlp(cleaned_text)
lemmatized_tokens = [token.lemma_ for token in doc if not token.is_punct]

custom_words = [' ', 'o', 'de', 'de o', 'em o', 'e', 'que', 'em']
lemmatized_tokens = [x for x in lemmatized_tokens if x not in custom_words]
pd.value_counts(np.array(lemmatized_tokens))

<ipython-input-48-faef4c99bfe4>:6: FutureWarning: pandas.value_counts is deprecated and will be removed in a future version. Use pd.Series(obj).value_counts() instead.
  pd.value_counts(np.array(lemmatized_tokens))
<ipython-input-48-faef4c99bfe4>:6: FutureWarning: The behavior of value_counts with object-dtype is deprecated. In a future version, this will *not* perform dtype inference on the resulting index. To retain the old behavior, use `result.index = result.index.infer_objects()`
  pd.value_counts(np.array(lemmatized_tokens))


ser           68
um            59
ter           38
gente         34
para          32
              ..
abrir          1
oito           1
tesourar       1
passo          1
disposição     1
Name: count, Length: 599, dtype: int64

In [ ]:
from gensim.models import Phrases
bigram = Phrases(tokens)
tokens = bigram[tokens]

## Train Model

In [ ]:
from gensim.corpora.dictionary import Dictionary
dictionary = Dictionary(processed_texts)

In [ ]:
corpus = [dictionary.doc2bow(text) for text in processed_texts]

In [ ]:
from gensim.models.ldamodel import LdaModel
lda_model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=5, passes=10)

## Tuning and Evaluate Model

In [ ]:
from gensim.models.coherencemodel import CoherenceModel
coherence_model = CoherenceModel(model=lda_model, texts=processed_texts, dictionary=dictionary, coherence='c_v')
coherence_score = coherence_model.get_coherence()

  error: subprocess-exited-with-error
  
  × python setup.py egg_info did not run successfully.
  │ exit code: 1
  ╰─> See above for output.
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
  Preparing metadata (setup.py) ... error
error: metadata-generation-failed

× Encountered error while generating package metadata.
╰─> See above for output.

note: This is an issue with the package mentioned above, not pip.
hint: See above for details.


# BERTopic

BERTopic calls for preprocessing but to a lesser extent than LDA.
The package is modular, that means you can reconfigure in order to get to better results.
There's a need for empirical assessment of which one works best, meaning trial and error of which hyperparameters work best

In [ ]:
!pip install bertopic
from bertopic import BERTopic

from gensim.corpora import Dictionary

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.7/143.7 kB 10.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.2/4.2 MB 72.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.8/88.8 kB 6.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.9/56.9 kB 3.7 MB/s eta 0:00:00


### Call Functions

In [ ]:
def not_within_bboxes(obj,bboxes):

    def obj_in_bbox(_bbox):
        v_mid = (obj["top"] + obj["bottom"]) / 2
        h_mid = (obj["x0"] + obj["x1"]) / 2
        x0, top, x1, bottom = _bbox
        return (h_mid >= x0) and (h_mid < x1) and (v_mid >= top) and (v_mid < bottom)

    return not any(obj_in_bbox(__bbox) for __bbox in bboxes)

# Extrai o texto de um arquivo PDF que não está dentro de tabelas ou figuras
def raw_text_extract(pdf_file, include_tables=False, include_images=False, show_page_number=False):
    page_data = []
    with pdfplumber.open(pdf_file) as pdf:
        for page in pdf.pages:
            #page = pdf.pages[0]

            if show_page_number:
                print(f"Pagina: {page.page_number}")

            #print(page.extract_text())
            bboxes = []
            # identificando as tabelas
            if not include_tables:
                bboxes = [
                    table.bbox
                    for table in page.find_tables(
                    table_settings={
                        "vertical_strategy": "lines",
                        "horizontal_strategy": "lines",
                        "explicit_vertical_lines": curves_to_edges(page.curves) + page.edges,
                        "explicit_horizontal_lines": curves_to_edges(page.curves) + page.edges,
                    }
                    )
                ]
            #print(bboxes)

            # identificando as imagens
            if not include_images:
                for image in page.images:
                    image_bbox = (image['x0'], image['top'], image['x1'], image['bottom'])
                    bboxes.append(image_bbox)
                    #print("img: ",image_bbox)

            # Filtrando os textos que estão fora das caixas das tabelas e das figuras
            page = page.filter(lambda obj: not_within_bboxes(obj, bboxes))

            # a arquivo bbdc-2015-3T-Transcrição da Teleconferência 3T15.pdf gera caracteres duplicados. Esse método resolve o problema.
            # ref: https://github.com/jsvine/pdfplumber/issues/71
            text = page.dedupe_chars().extract_text()


            ##### removendo cabeçalho: bbdc, bbas, prbc -> "Transc... ano": Pode ter ou não "Transcrição da"; Pode ter 3 ou 4 linhas

            # Transcrição da Teleconferência
            # Resultados do 4T09
            # Banco do Brasil (BBAS3 BZ) <- esta linha pode nao aparecer no BBDC
            # 26 de fevereiro de 2010

            # prbc-2013-2T13
            # Teleconferência do Paraná Banco
            # Resultados do 2° trimestre de 2013
            # 14 de junho de 2013 – 11h00 (horário de Brasília)
            text = re.sub(r"(Transcrição da )?Teleconferência(.*)?((?:\n|\r\n?)(.*))?((?:\n|\r\n?)(.*))?(?:\n|\r\n?)(.*)[0-9]{4}( – [0-9]{2}h(.*))?", '', text).strip()

            ##### Removendo cabeçalhos do ITUB
            # Itaú Unibanco
            # Resultados do Terceiro trimestre de 2018
            # 30 de outubro de 2018
            text = re.sub(r"Itaú Unibanco(.*)?((?:\n|\r\n?)(.*))?((?:\n|\r\n?)(.*))?(?:\n|\r\n?)(.*)[0-9]{4}", '', text).strip()

            ##### Removendo cabeçalhos do BBAS
            # - Palavra "#Pública" (3T19 a 3T22) e #interna (1T21 a 1T22)
            text = re.sub(f"#Pública", '', text).strip()

            # - Palavra "#interna" (1T21 a 1T22)
            text = re.sub(f"#interna", '', text).strip()


            # bbas-2006-4T06-Transcrição
            # Local Conference Call
            # Banco do Brasil Nac. – (29314)
            # Resultados do Exercício de 2006
            # 28 de Fevereiro de 2007 – 11:00h - horário local
            text = re.sub(r"Local Conference Call(?:\n|\r\n?)(.*)?((?:\n|\r\n?)(.*))?(?:\n|\r\n?)(.*)", '', text).strip()

            # bbas-2009-4T09-Transcrição.pdf
            # O padrão é este. As linhas iniciais são removidas na regra anterior, mas fica a linha da data, que é removida aqui
            # Transcrição da Teleconferência
            # Resultados do 4T09
            # Banco do Brasil (BBAS3 BZ)
            # 26 de fevereiro de 2010
            text = re.sub(r"^[0-9]{2}(.*)[0-9]{4}", '', text).strip()

            # Relação com Investidores
            # Transcrição 1T21
            # BANCO DO BRASIL
            # TELECONFERÊNCIA
            # DE RESULTADOS
            # 1T2021
            text = re.sub(r"Relação com Investidores(?:\n|\r\n?)(.*)?((?:\n|\r\n?)(.*))?((?:\n|\r\n?)(.*))?(?:\n|\r\n?)(.*)?(?:\n|\r\n?)(.*)", '', text).strip()

            # bbas-2020-3T20-Transcrição Teleconferência 3T20.pdf
            # BANCO DO BRASIL
            # TELECONFERÊNCIA
            # DE RESULTADOS
            # 3T2020
            # 06/11/2020
            text = re.sub(r"BANCO DO BRASIL(?:\n|\r\n?)(.*)?((?:\n|\r\n?)(.*))?((?:\n|\r\n?)(.*))?(?:\n|\r\n?)(.*)", '', text).strip()


            # removendo cabeçalho: abcb -> "Banco ABC Brasil | Relações com Investidores Transcrição da"
            text = re.sub(r"Banco ABC Brasil \| (.*)((?:\n|\r\n?))", '', text).strip()


            # removendo o número da página que veio junto do texto
            text = re.sub(f"\\n{page.page_number}$", '', text)

            text = re.sub(f'- {page.page_number} -', '', text)


            # removendo o número da página que veio junto do texto: bbdc -> "(cid:1) <pagina>"
            text = re.sub(f"\(cid:1\) {page.page_number}$", '', text).strip()

            # removendo o número da página que veio junto do texto: prbc -> "Página <pagina>"
            text = re.sub(f"Página {page.page_number}$", '', text).strip()

            # removendo o número da página que veio junto do texto: itub -> "1/12"
            text = re.sub(f'{page.page_number}/{len(pdf.pages)}$', '', text).strip()

            # removendo o número da página que veio junto do texto: itub -> "Teleconferência 4T21 2"
            text = re.sub(r'Teleconferência \dT\d{2} \d+$', '', text).strip()

            # removendo o número da página que veio junto do texto:
            # No abcp-2009-3T09, todas as páginas estão com número "9" e
            # no abcp-2009-3T09, todas as páginas estão com número 7
            head, tail = os.path.split(pdf_file)
            if (tail.startswith('abcb-2009')):
                if (tail.startswith('abcb-2009-3T09')):
                    text = re.sub(r'((?:\n|\r\n?))9$', '', text).strip()
                elif (tail.startswith('abcb-2009-4T09')):
                    text = re.sub(r'((?:\n|\r\n?))7$', '', text).strip()

            page_data.append(text)

    return page_data

In [ ]:
def clean_bert(text):

    text = text.replace("\n", ' ')
    text = text.replace("”", '')
    text = text.replace("“", '')
    text = text.replace("\"", '')
    text = text.replace("", '')

    #lista com bolinha
    text = re.sub(r'(\s)?(;\s)?(•)', "; ", text.strip())
    text = re.sub(r'(: ;)', ": ", text.strip())
    text = re.sub(r'(\.;)', ". ", text.strip())

    # nu-2021-4T21-Script 4T21.pdf
    text = re.sub(r'(; -)', ". ", text.strip())
    text = re.sub(r'(\. -)', ". ", text.strip())
    text = re.sub(r'^(-)', "", text.strip())
    text = re.sub(r'(: \d.)', ': .', text.strip())
    text = re.sub(r'(; e (\d+\.)?)', '.', text.strip())
    text = re.sub(r'(: ●)', '.', text.strip())
    text = re.sub(r'(; ●)', '.', text.strip())
    text = re.sub(r'(●)', '', text.strip())

    text = re.sub("_______________________________________________________________", "", text)

    text = re.sub(r"Sra\.", "Senhora ", text, flags=re.IGNORECASE)
    text = re.sub(r"Sr\.", "Senhor ", text, flags=re.IGNORECASE)
    text = re.sub(r"Srs\.", "Senhores ", text, flags=re.IGNORECASE)
    text = re.sub(r'b\.p\.\s([A-Z])', 'bp. \\1', text).strip()
    text = re.sub('b.p.', 'bp', text).strip()
    text = re.sub('p.p.', 'pp', text).strip()
    text = re.sub('help!', 'help', text).strip() # bmgb -> tirar a exclamação para evitar quebra de sentenças

    text = re.sub('\s+', ' ', text).strip() # deixar por ultimo, pois as substituicoes anteriores podem inserir multiplos espaços

    #text = re.sub(r'[^\w\s]', ' ', text)  # Removes punctuation
    text = re.sub(r'  ', ' ', text)
    text = text.lower()

    return text

### Processing text

In [ ]:
transcript_folder = '/content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/'
transcript_text_folder = "/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/"

if not os.path.exists(transcript_text_folder):
    os.mkdir(transcript_text_folder)

#Recupera os arquivos que estão na pasta
files = os.listdir(transcript_folder)
#files = files[0:2]

num_files = len(files)
for i, file in enumerate(files):
    path_transcription = transcript_folder + file

    file_name_parts = file.split("-")
    ticker          = file_name_parts[0].strip()
    trimestre       = file_name_parts[2].strip()

    path_folder_ticker = os.path.join(transcript_text_folder, ticker)

    print(path_folder_ticker, ticker, trimestre)
    print('path_transcription', path_transcription)
    if not os.path.exists(path_folder_ticker):
        os.mkdir(path_folder_ticker)

    print('is_file',os.path.isfile(path_transcription))
    if os.path.isfile(path_transcription):
      print(f"Processando arquivo {i+1} de {num_files}")

      print("*** Extraindo texto do PDF: "+ file)
      path_transcription = transcript_folder + file
      if ticker in ['bbas', 'bbdc']:
          page_data = raw_text_extract(path_transcription)
      else:
          page_data = raw_text_extract(path_transcription, include_tables=True, include_images=False)

      #print(page_data)

      print("*** Limpando o texto")
      text = " ".join(page_data)
      text = clean(text)

      file_path = f"{path_folder_ticker}/{ticker}-{file_name_parts[1]+'-'+trimestre}.txt"

      print("*** Salvando arquivo com a texto")
      with open(file_path, 'w', encoding='utf-8') as file:
          file.write(text)

### Call processed text

In [ ]:
transcript_folder = '/content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/'
transcript_text_folder = "/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/"

#Recupera os arquivos que estão na pasta
files = os.listdir(transcript_folder)
files = files[0:5]

texts_as_strings = []

num_files = len(files)
for i, file in enumerate(files):
    path_transcription = transcript_folder + file

    file_name_parts = file.split("-")
    ticker          = file_name_parts[0].strip()
    trimestre       = file_name_parts[2].strip()

    path_folder_ticker = os.path.join(transcript_text_folder, ticker)

    print(path_folder_ticker, ticker, trimestre)
    print('path_transcription', path_transcription)

    #print('is_file',os.path.isfile(path_transcription))
    if os.path.isfile(path_transcription):
      print(f"Processando arquivo {i+1} de {num_files}")

      print("*** Extraindo texto do PDF: "+ file)
      path_transcription = transcript_folder + file
      if ticker in ['bbas', 'bbdc']:
          page_data = raw_text_extract(path_transcription)
      else:
          page_data = raw_text_extract(path_transcription, include_tables=True, include_images=False)

      #print(page_data)

      print("*** Limpando o texto")
      text = " ".join(page_data)
      text = clean_bert(text)

      texts_as_strings.append(text)

#texts_as_strings[]

/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/abcb abcb 3T22
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
Processando arquivo 1 de 5
*** Extraindo texto do PDF: abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
*** Limpando o texto
/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/abcb abcb 2T10
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/abcb-2010-2T10-Transcrição da Teleconferência 2T10.pdf
Processando arquivo 2 de 5
*** Extraindo texto do PDF: abcb-2010-2T10-Transcrição da Teleconferência 2T10.pdf
*** Limpando o texto
/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/sanb sanb 3T
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/sanb-2015-3T-Transcrição Teleconfe

NameError: name 'curves_to_edges' is not defined

In [ ]:
dic_docs = {}
dic_docs['doc 1'] = texts_as_strings[0]
len(texts_as_strings)

3

In [ ]:
transcript_folder = '/content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/'

#Recupera os arquivos que estão na pasta
files = os.listdir(transcript_folder)
files = files[0:2]

texts_as_strings = []

num_files = len(files)
for i, file in enumerate(files):
    path_transcription = transcript_folder + file

    file_name_parts = file.split("-")
    ticker          = file_name_parts[0].strip()
    trimestre       = file_name_parts[2].strip()

    path_folder_ticker = os.path.join(transcript_text_folder, ticker)

    print(path_folder_ticker, ticker, trimestre)
    print('path_transcription', path_transcription)

    #print('is_file',os.path.isfile(path_transcription))
    if os.path.isfile(path_transcription):
      print(f"Processando arquivo {i+1} de {num_files}")

      print("*** Extraindo texto do PDF: "+ file)
      path_transcription = transcript_folder + file
      if ticker in ['bbas', 'bbdc']:
          page_data = raw_text_extract(path_transcription)
      else:
          page_data = raw_text_extract(path_transcription, include_tables=True, include_images=False)

      #print(page_data)

      print("*** Limpando o texto")
      text = " ".join(page_data)
      #text = clean_bert(text)

      print(text)


/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/abcb abcb 3T22
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
Processando arquivo 1 de 2
*** Extraindo texto do PDF: abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
*** Limpando o texto
CONFERÊNCIA DE RESULTADOS DO BANCO ABC BRASIL
3° TRIMESTRE DE 2022
7 de novembro de 2022
Sr. Ricardo Moura: Bom dia a todos, eu sou o Ricardo Moura, Diretor de Relações com
Investidores e M&A Proprietário. Sejam bem-vindos à teleconferência de resultados do
terceiro trimestre de 2022 do Banco ABC Brasil.
Para quem está assistindo a transmissão via Zoom e deseja acompanhar em inglês, por
favor, cliquem no botão de tradução à direita e abaixo de sua tela.
Antes de iniciarmos, gostaríamos de compartilhar seguintes disclaimers:
Eventuais declarações que possam ser feitas durante esta con

### Application

In [ ]:
from sentence_transformers import SentenceTransformer

# Load a Sentence-Transformer model
embedding_model = SentenceTransformer('paraphrase-multilingual-mpnet-base-v2')

In [ ]:
from bertopic import BERTopic
import hdbscan
from umap import UMAP

# Custom UMAP
umap_model = UMAP(n_neighbors=15,
                  n_components=5,
                  min_dist=0.0,
                  metric='cosine',
                  random_state=42)

# Custom HDBSCAN
hdbscan_model = hdbscan.HDBSCAN(min_cluster_size=10,
                                metric='euclidean',
                                cluster_selection_method='eom',
                                prediction_data=True)

# Initialize BERTopic with custom models
topic_model = BERTopic(embedding_model=embedding_model,
                       umap_model=umap_model,
                       hdbscan_model=hdbscan_model,
                       language="portuguese",
                       calculate_probabilities=True,
                       verbose=True)


In [ ]:
topic_info = topic_model.get_topic_info()
print(topic_info.head())  # Shows topic IDs and sizes

In [ ]:
# Inspect a specific topic
topic_words = topic_model.get_topic(0)
print(topic_words)

### Visualization

In [ ]:
fig = topic_model.visualize_topics()
fig.show()

In [ ]:
fig = topic_model.visualize_heatmap()
fig.show()

In [ ]:

topics, probs = topic_model.fit_transform(documents)

# To visualize the hierarchy:
fig = topic_model.visualize_hierarchy()
fig.show()

### Paragraph-level Analysis

#### Call Functions

In [ ]:
from sentence_transformers import SentenceTransformer

# Load a Sentence-Transformer model
embedding_model = SentenceTransformer('paraphrase-multilingual-mpnet-base-v2')

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/4.13k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/723 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/402 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.08M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [ ]:
!pip install bertopic
from bertopic import BERTopic

from gensim.corpora import Dictionary
#from transformers import FinBERT

In [ ]:
def raw_text_extract_with_paragraphs(pdf_file, include_tables=False, include_images=False, show_page_number=False):
    page_data = []
    raw_text = []
    with pdfplumber.open(pdf_file) as pdf:
        for page in pdf.pages:

            if show_page_number:
                print(f"Pagina: {page.page_number}")

            bboxes = []
            if not include_tables:
                bboxes = [
                    table.bbox
                    for table in page.find_tables(
                        table_settings={
                            "vertical_strategy": "lines",
                            "horizontal_strategy": "lines",
                            "explicit_vertical_lines": curves_to_edges(page.curves) + page.edges,
                            "explicit_horizontal_lines": curves_to_edges(page.curves) + page.edges,
                        }
                    )
                ]

            if not include_images:
                for image in page.images:
                    image_bbox = (image['x0'], image['top'], image['x1'], image['bottom'])
                    bboxes.append(image_bbox)

            # Filter out text within tables or images
            page = page.filter(lambda obj: not_within_bboxes(obj, bboxes))
            text = page.dedupe_chars().extract_text()

            #raw_texts = text

            # Preprocess text to clean headers and footers
            # Add your specific text cleaning rules here, as in the original code

            # Combine single line breaks into paragraphs, retain multiple line breaks
            #text = text.replace("\n", " ").replace("\r\n", " ")  # Replace single breaks with spaces
            text = re.sub(r'(?<!\n)\n(?!\n)', ' ', text)

            #first_sub = text

            #paragraphs = [p.strip() for p in re.split(r'\n{2,}', text) if p.strip()]  # Split by multiple \n

            page_data.append(text)
            #raw_text.append(raw_texts)

    return page_data#, raw_text, first_sub


In [ ]:
transcript_folder = '/content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/'
transcript_text_folder = "/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/"

#Recupera os arquivos que estão na pasta
files = os.listdir(transcript_folder)
files = files#[0:1]

texts_as_strings = []

num_files = len(files)
for i, file in enumerate(files):
    path_transcription = transcript_folder + file

    file_name_parts = file.split("-")
    print(file_name_parts)
    ticker          = file_name_parts[0].strip()
    trimestre       = file_name_parts[2].strip()

    path_folder_ticker = os.path.join(transcript_text_folder, ticker)

    print(path_folder_ticker, ticker, trimestre)
    print('path_transcription', path_transcription)

    #print('is_file',os.path.isfile(path_transcription))
    if os.path.isfile(path_transcription):
      print(f"Processando arquivo {i+1} de {num_files}")

      print("*** Extraindo texto do PDF: "+ file)
      path_transcription = transcript_folder + file
      if ticker in ['bbas', 'bbdc']:
          page_data = raw_text_extract_with_paragraphs(path_transcription)
      else:
          page_data = raw_text_extract_with_paragraphs(path_transcription, include_tables=True, include_images=False)

      #print(page_data)

      print("*** Limpando o texto")
      #text = " ".join(page_data)
      #text = clean_bert(text)

      texts_as_strings.append(page_data)

['abcb', '2022', '3T22', 'Banco ABC Brasil ', ' Transcrição Teleconferencia 3T22 PT.pdf']
/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/abcb abcb 3T22
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
Processando arquivo 1 de 384
*** Extraindo texto do PDF: abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
*** Limpando o texto
['abcb', '2010', '2T10', 'Transcrição da Teleconferência 2T10.pdf']
/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/abcb abcb 2T10
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/abcb-2010-2T10-Transcrição da Teleconferência 2T10.pdf
Processando arquivo 2 de 384
*** Extraindo texto do PDF: abcb-2010-2T10-Transcrição da Teleconferência 2T10.pdf
*** Limpando o texto
['sanb', '2015', '3T', 'Transcrição Teleconfere

#### Application

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
stop_word_list = list(portuguese_stop_words)
stop_word_list = stop_word_list + ['sr','gente','trimestre', 'obrigado', 'agora', 'aqui', 'né', 'então', 'ano']
#print(stop_word_list)
vectorizer_model = CountVectorizer(ngram_range=(1, 2), stop_words=stop_word_list)

embedding_model = SentenceTransformer('paraphrase-multilingual-mpnet-base-v2')

In [ ]:
# Flatten into a single list of chunks
docs = [chunk for doc in texts_as_strings for chunk in doc]

In [ ]:
import json

with open("/content/drive/MyDrive/Portfolio Projects/Mestrado/Temp/chunks.json", 'r') as f:
    docs = json.load(f)

In [ ]:
import torch
torch.cuda.is_available()

True

In [ ]:
device = "cuda:0" if torch.cuda.is_available() else "cpu"

In [ ]:
from sentence_transformers import SentenceTransformer

# Download and load the BERTimbau 'base' model
model_name = "neuralmind/bert-base-portuguese-cased"
pt_model = SentenceTransformer(model_name)

/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/647 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/438M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/43.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/210k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/2.00 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

In [ ]:
pt_model = pt_model.to('cuda:0')

In [ ]:
embeddings = pt_model.encode(docs, show_progress_bar=True)

Batches:   0%|          | 0/188 [00:00<?, ?it/s]

In [ ]:
from bertopic import BERTopic
import hdbscan
from umap import UMAP

# Custom UMAP
umap_model = UMAP(n_neighbors=5,
                  n_components=10,
                  min_dist=0.01,
                  metric='cosine',
                  random_state=42)

# Custom HDBSCAN
hdbscan_model = hdbscan.HDBSCAN(min_cluster_size=5,
                                min_samples=5,
                                metric='euclidean',
                                cluster_selection_method='eom',
                                prediction_data=True)

# Initialize BERTopic with custom models
topic_model = BERTopic(#embedding_model=embedding_model,
                       umap_model=umap_model,
                       hdbscan_model=hdbscan_model,
                       vectorizer_model=vectorizer_model,
                       language="portuguese",
                       calculate_probabilities=True,
                       verbose=True)


In [ ]:
topics, probs = topic_model.fit_transform(docs, embeddings)

NameError: name 'topic_model' is not defined

In [ ]:
topic_info = topic_model.get_topic_info()
print(topic_info.head())  # Shows topic IDs and sizes

In [ ]:
topic_info.Representation[0]

In [ ]:
import json
with open("/content/drive/MyDrive/Portfolio Projects/Mestrado/Temp/chunks.json", 'w') as f:
    # indent=2 is not needed but makes the file human-readable
    # if the data is nested
    json.dump(docs, f, indent=2)

#### PyPDF2

In [ ]:
!pip install PyPDF2
from PyPDF2 import PdfReader

def pdf_to_text_pypdf2(pdf_file):
    """
    Extracts text from a PDF file using PyPDF2.

    :param pdf_file: Path to the PDF file
    :return: A string containing the extracted text
    """
    try:
        # Initialize the PDF reader
        reader = PdfReader(pdf_file)
        all_text = []

        # Iterate through each page
        for page in reader.pages:
            # Extract text from the page
            text = page.extract_text()
            if text:  # Avoid adding None if the page has no text
                all_text.append(text)

        # Combine all pages into a single string
        return "\n".join(all_text)

    except Exception as e:
        print(f"Error while processing the PDF: {e}")
        return None

# Example usage
#pdf_file_path = "your_pdf_file.pdf"
#extracted_text = pdf_to_text_pypdf2(pdf_file_path)

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 3.4 MB/s eta 0:00:00


In [ ]:
transcript_folder = '/content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/'
transcript_text_folder = "/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/"

#Recupera os arquivos que estão na pasta
files = os.listdir(transcript_folder)
files = files[0:1]

texts_as_strings = []

num_files = len(files)
for i, file in enumerate(files):
    path_transcription = transcript_folder + file

    file_name_parts = file.split("-")
    print(file_name_parts)
    ticker          = file_name_parts[0].strip()
    trimestre       = file_name_parts[2].strip()

    path_folder_ticker = os.path.join(transcript_text_folder, ticker)

    print(path_folder_ticker, ticker, trimestre)
    print('path_transcription', path_transcription)

    #print('is_file',os.path.isfile(path_transcription))
    if os.path.isfile(path_transcription):
      print(f"Processando arquivo {i+1} de {num_files}")

      print("*** Extraindo texto do PDF: "+ file)
      path_transcription = transcript_folder + file

      page_data = extracted_text = pdf_to_text_pypdf2(path_transcription)

      texts_as_strings.append(page_data)

['abcb', '2022', '3T22', 'Banco ABC Brasil ', ' Transcrição Teleconferencia 3T22 PT.pdf']
/content/drive/MyDrive/Portfolio Projects/Mestrado/transcricoes_processadas_BERTopic/abcb abcb 3T22
path_transcription /content/drive/MyDrive/Portfolio Projects/Mestrado/Transcripts/abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf
Processando arquivo 1 de 1
*** Extraindo texto do PDF: abcb-2022-3T22-Banco ABC Brasil - Transcrição Teleconferencia 3T22 PT.pdf


In [ ]:
#re.sub(r'(?<!\n)\n(?!\n)', ' ', texts_as_strings[0])

paragraphs = [p.strip() for p in re.split(r'\n{2,}', texts_as_strings[0]) if p.strip()]  # Split by multiple \n
#paragraphs[:1000]
texts_as_strings[0]

" \n \n   \nCONFERÊNCIA DE RESULTADOS DO BANCO ABC  BRASIL  \n3° TRIMESTRE DE 202 2 \n7 de novembro  de 202 2 \n \nSr. Ricardo Moura : Bom dia a todos, eu sou o Ricardo Moura, Diretor de Relações com \nInvestidores e M&A Proprietário. Sejam bem -vindos à teleconferência de resultados do  \nterceiro  trimestre de 2022 do Banco ABC Brasil.  \nPara quem está assistindo a transmissão via Zoom e deseja  acompanhar em inglês, por \nfavor, cliquem no botão de tradução à direita e abaixo de sua tela.  \nAntes de iniciarmos, gostaríamos de compartilhar seguintes  disclaimers:  \nEventuais declarações que possam ser feitas durante esta conferência, relativas às \nperspectivas de negócios do Banco ABC Brasil, projeções, metas operacionais e \nfinanceiras, constituem -se em crenças e premissas da Administração da Companhia, \nbem como em informações atualmente disponíveis para  o Banco ABC Brasil. \nConsiderações futuras não são  garantia de desempenho e envolvem riscos, incertezas e \npremissas, 